In [ ]:
import numpy as np
import matplotlib.pyplot as plt

In [ ]:
import obspy as op
import cartopy.crs as ccrs
from obspy.clients.fdsn import Client
import cartopy.feature as cfeature
import cartopy.io.img_tiles as cimgt

%matplotlib inline
%config InlineBackend.figure_format = 'retina'

%matplotlib qt
from matplotlib.animation import FFMpegWriter

In [ ]:
minLat = 45    # I zoom in on the western Atlantic here
maxLat = 5
minLon = -100
maxLon = -40

# Hurricane Nicole (Nov. 6-11, 2022)

In [ ]:
data = np.loadtxt('hurricane_data.txt', skiprows=(46304), usecols=(1,2,3,4,5))
date = ""
time = data[:, 0]
timeElapsed = 0
lat = []
long = []
windSpeed = []
radius = []

In [ ]:
metadata = dict(title='Independent Project animation1', artist='Matplotlib')
writer = FFMpegWriter(fps=15, metadata=metadata)
fig = plt.figure(figsize=(60*1.5,40*1.5))

ax = fig.add_subplot(1, 1, 1, projection=ccrs.PlateCarree())
ax.set_extent([minLon,maxLon,minLat,maxLat], crs=ccrs.PlateCarree())
request = cimgt.GoogleTiles(style='satellite')

with writer.saving(fig, "animation1.mp4", dpi=200):
    for ts in range(0, 26):
        lat.append(data[ts, 1])
        long.append(data[ts, 2])
        windSpeed.append(data[ts, 3])
        radius.append(data[ts, 4] / 2)
        if ts <= 1:
            date = "6 Nov, 2022"
        elif ts > 1 and ts <= 5:
            date = "7 Nov, 2022"
        elif ts > 5 and ts <= 9:
            date = "8 Nov, 2022"
        elif ts > 9 and ts <= 15:
            date = "9 Nov, 2022"
        elif ts > 15 and ts <= 21:
            date = "10 Nov, 2022"
        else:
            date = "11 Nov, 2022"
            
        if ts > 0:
            timeElapsed += abs(time[ts] - time[ts-1])
            
        fig.clear()
        ax = fig.add_subplot(1, 1, 1, projection=ccrs.PlateCarree())
        ax.set_extent([minLon,maxLon,minLat,maxLat], crs=ccrs.PlateCarree())
        
        ax.add_image(request, 4)
        ax.text(-98, 10, date, backgroundcolor = 'k', color='w', fontfamily = 'monospace', fontsize='large')
        ax.text(-89, 10, int(time[ts]), backgroundcolor = 'k', c='w', fontfamily = 'monospace', fontsize='large')
        ax.text(-98, 8, 'Time since storm began:', backgroundcolor = 'k', c='w', fontfamily = 'monospace', fontsize='large')
        ax.text(-83, 8, int(timeElapsed/100), backgroundcolor = 'k', c='w', fontfamily = 'monospace', fontsize='large')
        ax.text(-80.5, 8, 'hours', backgroundcolor = 'k', c='w', fontfamily = 'monospace', fontsize='large')
       
        stormPath = ax.scatter(long, lat, c=windSpeed, s=radius, cmap='plasma', transform=ccrs.PlateCarree())
       
        cbar = plt.colorbar(stormPath, shrink=0.5)
        cbar.set_label('Wind speed', fontsize=25)
        cbar.ax.tick_params(labelsize=25)
       
        plt.show()
        plt.draw()
        plt.pause(0.001)
        writer.grab_frame()

# All hurricanes from 2021-2022

In [ ]:
data = np.loadtxt('hurricane_data.txt', skiprows=(45221), usecols=(1,2,3,4,5))
time = np.array(data[:, 0])
lat = np.array([])
long = np.array([])
windSpeed = np.array([])
radius = np.array([])

latCumulative = np.array([])
longCumulative = np.array([])
windCumulative = np.array([])
radiusCumulative = np.array([])

In [ ]:
metadata = dict(title='Independent Project animation2', artist='Matplotlib')
writer = FFMpegWriter(fps=15, metadata=metadata)
fig = plt.figure(figsize=(60*1.5,40*1.5))

ax = fig.add_subplot(1, 1, 1, projection=ccrs.PlateCarree())
ax.set_extent([minLon,maxLon,minLat,maxLat], crs=ccrs.PlateCarree())
request = cimgt.GoogleTiles(style='satellite')

count = 0
timeElapsed = 0

with writer.saving(fig, "animation2.mp4", dpi=200):
    for ts in range(0, 1108):
        if data[ts, 2] == 0:                    #denotes the end of one storm and beginning of another
            latCumulative = np.append(latCumulative, lat)
            longCumulative = np.append(longCumulative, long)
            windCumulative = np.append(windCumulative, windSpeed)
            radiusCumulative = np.append(radiusCumulative, radius)
            
            lat = np.array([])
            long = np.array([])
            windSpeed = np.array([])
            radius = np.array([])
            
            count = 0
            timeElapsed = 0
        
        lat = np.append(lat, data[ts, 1])
        long = np.append(long, data[ts, 2])
        windSpeed = np.append(windSpeed, data[ts, 3])
        radius = np.append(radius, data[ts, 4] / 2)
        
        if count > 0:
            timeElapsed += abs(time[ts] - time[ts-1])
            
        fig.clear()
        ax = fig.add_subplot(1, 1, 1, projection=ccrs.PlateCarree())
        ax.set_extent([minLon,maxLon,minLat,maxLat], crs=ccrs.PlateCarree())
        
        ax.add_image(request, 4)
        ax.text(-98, 8, 'Time since current storm began:', backgroundcolor = 'k', c='w', fontfamily = 'monospace', 
                fontsize='large')
        ax.text(-77, 8, int(timeElapsed/100), backgroundcolor = 'k', c='w', fontfamily = 'monospace', fontsize='large')
        ax.text(-74.5, 8, 'hours', backgroundcolor = 'k', c='w', fontfamily = 'monospace', fontsize='large')
        
        stormPath = ax.scatter(long, lat, c=windSpeed, s=radius, cmap='plasma', transform=ccrs.PlateCarree())
        ax.scatter(longCumulative, latCumulative, c='silver', s=radiusCumulative, transform=ccrs.PlateCarree())

        cbar = plt.colorbar(stormPath, shrink=0.5)
        cbar.set_label('Wind speed', fontsize=25)
        cbar.ax.tick_params(labelsize=25)
        
        plt.show()
        plt.draw()
        plt.pause(0.001)
        writer.grab_frame()
        
        count += 1

# Comparing storms from 1851, 1936, and 2022

In [ ]:
data1851 = np.loadtxt('hurricane_data1851.txt', skiprows=(1), usecols=(1,2,3,4))
data1936 = np.loadtxt('hurricane_data1936.txt', skiprows=(1), usecols=(1,2,3,4))
data2022 = np.loadtxt('hurricane_data2022.txt', skiprows=(1), usecols=(1,2,3,4))

time1851 = np.array(data1851[:, 0])
time1936 = np.array(data1936[:, 0])
time2022 = np.array(data2022[:, 0])
lat = np.array([])
long = np.array([])
windSpeed = np.array([])

latCumulative1851 = np.array([])
longCumulative1851 = np.array([])
windCumulative1851 = np.array([])

latCumulative1936 = np.array([])
longCumulative1936 = np.array([])
windCumulative1936 = np.array([])

latCumulative2022 = np.array([])
longCumulative2022 = np.array([])
windCumulative2022 = np.array([])

In [ ]:
metadata = dict(title='Independent Project animation3', artist='Matplotlib')
writer = FFMpegWriter(fps=15, metadata=metadata)
fig = plt.figure(figsize=(60*1.5,40*1.5))

ax = fig.add_subplot(1, 1, 1, projection=ccrs.PlateCarree())
ax.set_extent([minLon,maxLon,minLat,maxLat], crs=ccrs.PlateCarree())
request = cimgt.GoogleTiles(style='satellite')


with writer.saving(fig, "animation3.mp4", dpi=200):
    #1851
    count = 0
    timeElapsed = 0
    
    for ts in range(0, 102):
        if data1851[ts, 2] == 0.0:                    #denotes the end of one storm and beginning of another
            latCumulative1851 = np.append(latCumulative1851, lat)
            longCumulative1851 = np.append(longCumulative1851, long)
            windCumulative1851 = np.append(windCumulative1851, windSpeed)
            
            lat = np.array([])
            long = np.array([])
            windSpeed = np.array([])
            
            count = 0
            timeElapsed = 0
        
        lat = np.append(lat, data1851[ts, 1])
        long = np.append(long, data1851[ts, 2])
        windSpeed = np.append(windSpeed, data1851[ts, 3])
        
        if count > 0:
            timeElapsed += abs(time1851[ts] - time1851[ts-1])
            
        fig.clear()
        ax = fig.add_subplot(1, 1, 1, projection=ccrs.PlateCarree())
        ax.set_extent([minLon,maxLon,minLat,maxLat], crs=ccrs.PlateCarree())
        
        ax.add_image(request, 4)
        ax.text(-98, 8, 'Time since current storm began:', backgroundcolor = 'k', c='w', fontfamily = 'monospace', 
                fontsize='large')
        ax.text(-77, 8, int(timeElapsed/100), backgroundcolor = 'k', c='w', fontfamily = 'monospace', fontsize='large')
        ax.text(-74.5, 8, 'hours', backgroundcolor = 'k', c='w', fontfamily = 'monospace', fontsize='large')
        
        stormPath = ax.scatter(long, lat, s=35.0, c=windSpeed, cmap='plasma', transform=ccrs.PlateCarree())
        storms1851 = ax.scatter(longCumulative1851, latCumulative1851, s=35.0, c='silver', transform=ccrs.PlateCarree())
        
        stormPath.set_label('Current storm')
        storms1851.set_label('1851 storms')
        ax.legend()

        cbar = plt.colorbar(stormPath, shrink=0.5)
        cbar.set_label('Wind speed', fontsize=25)
        cbar.ax.tick_params(labelsize=25)
        
        plt.show()
        plt.draw()
        plt.pause(0.001)
        writer.grab_frame()
        
        count += 1
        
        
        
        
    #1936
    count = 0
    timeElapsed = 0

    for ts in range(0, 195):
        if data1936[ts, 2] == 0:                    #denotes the end of one storm and beginning of another
            latCumulative1936 = np.append(latCumulative1936, lat)
            longCumulative1936 = np.append(longCumulative1936, long)
            windCumulative1936 = np.append(windCumulative1936, windSpeed)
            
            lat = np.array([])
            long = np.array([])
            windSpeed = np.array([])
            
            count = 0
            timeElapsed = 0
        
        lat = np.append(lat, data1936[ts, 1])
        long = np.append(long, data1936[ts, 2])
        windSpeed = np.append(windSpeed, data1936[ts, 3])
        
        if count > 0:
            timeElapsed += abs(time1936[ts] - time1936[ts-1])
            
        fig.clear()
        ax = fig.add_subplot(1, 1, 1, projection=ccrs.PlateCarree())
        ax.set_extent([minLon,maxLon,minLat,maxLat], crs=ccrs.PlateCarree())
        
        ax.add_image(request, 4)
        ax.text(-98, 8, 'Time since current storm began:', backgroundcolor = 'k', c='w', fontfamily = 'monospace', 
                fontsize='large')
        ax.text(-77, 8, int(timeElapsed/100), backgroundcolor = 'k', c='w', fontfamily = 'monospace', fontsize='large')
        ax.text(-74.5, 8, 'hours', backgroundcolor = 'k', c='w', fontfamily = 'monospace', fontsize='large')
        
        stormPath = ax.scatter(long, lat, s=35.0, c=windSpeed, cmap='plasma', transform=ccrs.PlateCarree())
        storms1851 = ax.scatter(longCumulative1851, latCumulative1851, s=35.0, c='silver', transform=ccrs.PlateCarree())
        storms1936 = ax.scatter(longCumulative1936, latCumulative1936, s=35.0, c='fuchsia', transform=ccrs.PlateCarree())

        stormPath.set_label('Current storm')
        storms1851.set_label('1851 storms')
        storms1936.set_label('1936 storms')
        ax.legend()
        
        cbar = plt.colorbar(stormPath, shrink=0.5)
        cbar.set_label('Wind speed', fontsize=25)
        cbar.ax.tick_params(labelsize=25)
        
        plt.show()
        plt.draw()
        plt.pause(0.001)
        writer.grab_frame()
        
        count += 1
        

        
    #2022
    count = 0
    timeElapsed = 0

    for ts in range(0, 125):
        if data2022[ts, 2] == 0:                    #denotes the end of one storm and beginning of another
            latCumulative2022 = np.append(latCumulative2022, lat)
            longCumulative2022 = np.append(longCumulative2022, long)
            windCumulative2022 = np.append(windCumulative2022, windSpeed)
            
            lat = np.array([])
            long = np.array([])
            windSpeed = np.array([])
            
            count = 0
            timeElapsed = 0
        
        lat = np.append(lat, data2022[ts, 1])
        long = np.append(long, data2022[ts, 2])
        windSpeed = np.append(windSpeed, data2022[ts, 3])
        
        if count > 0:
            timeElapsed += abs(time2022[ts] - time2022[ts-1])
            
        fig.clear()
        ax = fig.add_subplot(1, 1, 1, projection=ccrs.PlateCarree())
        ax.set_extent([minLon,maxLon,minLat,maxLat], crs=ccrs.PlateCarree())
        
        ax.add_image(request, 4)
        ax.text(-98, 8, 'Time since current storm began:', backgroundcolor = 'k', c='w', fontfamily = 'monospace', 
                fontsize='large')
        ax.text(-77, 8, int(timeElapsed/100), backgroundcolor = 'k', c='w', fontfamily = 'monospace', fontsize='large')
        ax.text(-74.5, 8, 'hours', backgroundcolor = 'k', c='w', fontfamily = 'monospace', fontsize='large')
        
        stormPath = ax.scatter(long, lat, s = 35.0, c=windSpeed, cmap='plasma', transform=ccrs.PlateCarree())
        storms1851 = ax.scatter(longCumulative1851, latCumulative1851, s = 35.0, c='silver', transform=ccrs.PlateCarree())
        storms1936 = ax.scatter(longCumulative1936, latCumulative1936, s = 35.0, c='fuchsia', transform=ccrs.PlateCarree())
        storms2022 = ax.scatter(longCumulative2022, latCumulative2022, s = 35.0, c='cyan', transform=ccrs.PlateCarree())

        stormPath.set_label('Current storm')
        storms1851.set_label('1851 storms')
        storms1936.set_label('1936 storms')
        storms2022.set_label('2022 storms')
        ax.legend()
        
        cbar = plt.colorbar(stormPath, shrink=0.5)
        cbar.set_label('Wind speed', fontsize=25)
        cbar.ax.tick_params(labelsize=25)
        
        plt.show()
        plt.draw()
        plt.pause(0.001)
        writer.grab_frame()
        
        count += 1